In [3]:
import pandas as pd
import numpy as np
import math
import re

In [4]:
import requests
from pandas.io.json import json_normalize
import geopandas as gpd
from sklearn.cluster import KMeans
from shapely.geometry import Polygon, LineString, Point
from shapely.ops  import transform

In [5]:
# Matplotlib and associated plotting modules
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
#from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 geopandas=0.4.1 --yes 
import folium # map rendering library

Create a map of Edinburgh, split into its natural neighbourhoods.
https://python-visualization.github.io/folium/quickstart.html This is a link for my use later when I want to colour code the map based on similarity.

In [9]:
#url = ("https://opendata.arcgis.com/datasets/9961be54aa5649aebfb5f2cde53fa432_27.geojson")  #dataset for natural neighbourhoods in Edinburgh from Edinburgh City Council
#neighbourhoods = gpd.read_file(url)
#print(neighbourhoods.head())

   OBJECTID             NATURALCOM  OID_  CNT_NATURA  DUMMY_  SUM_ELECNO  \
0         1  Brunstane/Gilberstoun  1485        1485    1485     1485.30   
1         2           Newcraighall   262         262     262      261.77   
2         3              Magdalene  1479        1479    1479     1478.53   
3         4              Newbridge   327         327     327      326.84   
4         5     Cammo/Strathalmond   874         874     874      873.59   

   Z009_ELEC     Shapearea      Shapelen  \
0       1485  1.147451e+06   4629.409487   
1        262  4.414281e+05   3515.734273   
2       1479  3.119711e+05   2590.027278   
3        327  5.567828e+06  11661.263206   
4        874  2.008664e+06   7150.150690   

                                            geometry  
0  POLYGON ((-3.10276 55.94435, -3.10276 55.94435...  
1  MULTIPOLYGON (((-3.09979 55.93598, -3.09855 55...  
2  POLYGON ((-3.10240 55.94088, -3.10245 55.94165...  
3  POLYGON ((-3.41296 55.95159, -3.41414 55.95153...  
4  

In [6]:
url = (
    "https://opendata.arcgis.com/datasets/9961be54aa5649aebfb5f2cde53fa432_27.geojson" #dataset for natural neighbourhoods in Edinburgh from Edinburgh City Council
)
natural_neighbourhoods = f"{url}"


m = folium.Map(
    location=[55.9533, -3.1883],
    tiles="cartodbpositron",
    zoom_start=13,
)

shapes = folium.GeoJson(natural_neighbourhoods, name="geojson")

shapes.add_to(m)
    
folium.LayerControl().add_to(m)

m

https://geopandas.readthedocs.io/en/latest/gallery/polygon_plotting_with_folium.html example I used to help with the next cell.

In [16]:
path = "https://opendata.arcgis.com/datasets/9961be54aa5649aebfb5f2cde53fa432_27.geojson"
df = gpd.read_file(path)

m = folium.Map(location=[55.9533, -3.1883], zoom_start=10, tiles='CartoDB positron')

for _, r in df.iterrows():
    sim_geo = gpd.GeoSeries(r['geometry'])
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j,
                           style_function=lambda x: {'fillColor': 'orange'})
    folium.Popup(r['NATURALCOM']).add_to(geo_j)
    geo_j.add_to(m)

df = df.to_crs(epsg=2163) #set to a projected crs for centroid calculation accuracy.
df['centroids']=df.centroid.to_crs(epsg=4326)
df['lat'] = df['centroids'].y
df['lon'] = df['centroids'].x
df = df.to_crs(epsg=4326)

for _, r in df.iterrows():
    yo = folium.Marker(location=[r['lat'], r['lon']], popup='Name: {}'.format(r['NATURALCOM']))
    yo.add_to(m)
print(df)
m

     OBJECTID                 NATURALCOM  OID_  CNT_NATURA  DUMMY_  \
0           1      Brunstane/Gilberstoun  1485        1485    1485   
1           2               Newcraighall   262         262     262   
2           3                  Magdalene  1479        1479    1479   
3           4                  Newbridge   327         327     327   
4           5         Cammo/Strathalmond   874         874     874   
..        ...                        ...   ...         ...     ...   
149       150    Corstorphine/Craigmount  9799        9799    9799   
150       151               Corstorphine  9799        9799    9799   
151       152      Corstorphine/Clerwood  9799        9799    9799   
152       153  The Christians/Portobello  3535        3535    3535   
153       154      Ferryfield/Inverleith  3228        3228    3228   

     SUM_ELECNO  Z009_ELEC     Shapearea      Shapelen  \
0       1485.30       1485  1.147451e+06   4629.409487   
1        261.77        262  4.414281e+05   

In [9]:
CLIENT_ID = "K0K1215GLOMPN31CWAJTTG2MEXDNRZ2UJ1B1PYU0DXCCI3QZ"
CLIENT_SECRET = "E2ROHURCBVBBDLKJQ0MA4L0LQCSXYXLQJFZWVF0QAN3OJMHD"
VERSION = '20180605'
LIMIT = 100

In [38]:


def getNearbyVenues(names, latitudes, longitudes, area):
    
    venues_list=[]
    for name, lat, lng, area2 in zip(names, latitudes, longitudes, area):
        
        radius = 2*math.sqrt(area2/3) #factor of two to account for weirdly shaped areas. This makes a circle with twice the radius of the circle of the same area as the shape.
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/search?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&categoryId=4d4b7105d754a06374d81259'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng,
            radius,
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['venues']
        #print(results)
        
        # return only relevant information for each nearby venue
        venues_list.append([[name, lat, lng, v['id'],v['name'], v['location']['lat'], v['location']['lng'], v['categories'][0]['name']] for v in results])
        
        
            

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude',
                  'Venue ID',
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [39]:
edinburgh_venues = getNearbyVenues(names=df['NATURALCOM'],
                                   latitudes=df['lat'],
                                   longitudes=df['lon'],
                                   area = df['Shapearea']
                                  )
edinburgh_venues.head()

Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0  Brunstane/Gilberstoun               55.940545                 -3.09246   
1  Brunstane/Gilberstoun               55.940545                 -3.09246   
2  Brunstane/Gilberstoun               55.940545                 -3.09246   
3  Brunstane/Gilberstoun               55.940545                 -3.09246   
4  Brunstane/Gilberstoun               55.940545                 -3.09246   

                   Venue ID               Venue  Venue Latitude  \
0  54b97471498e26d1ad55ee73            Bar Zest       55.944542   
1  51483ee8e4b06af4b55605bb  kingsminor bistrot       55.945272   
2  4c4c67949e6dbe9a15c9700d    Porto Restaurant       55.946333   
3  4bd0525e046076b02fb36f71        Costa Coffee       55.933625   
4  54982260498ec9dc36acb134            Chiquito       55.934879   

   Venue Longitude        Venue Category  
0        -3.096077             Gastropub  
1        -3.096003        Breakfast Spot  
2        -3.084878  Fast Food Restaurant  
3        -3.105237           Coffee Shop  
4        -3.105460    Mexican Restaurant

Next I need to clean up the dataframe to take out venues that are not inside the neighbourhood boundaries.

In [40]:
edinburgh_venues_geo = gpd.GeoDataFrame(edinburgh_venues, geometry = gpd.points_from_xy(edinburgh_venues["Venue Longitude"],edinburgh_venues["Venue Latitude"]))
edinburgh_venues_geo.head()


Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0  Brunstane/Gilberstoun               55.940545                 -3.09246   
1  Brunstane/Gilberstoun               55.940545                 -3.09246   
2  Brunstane/Gilberstoun               55.940545                 -3.09246   
3  Brunstane/Gilberstoun               55.940545                 -3.09246   
4  Brunstane/Gilberstoun               55.940545                 -3.09246   

                   Venue ID               Venue  Venue Latitude  \
0  54b97471498e26d1ad55ee73            Bar Zest       55.944542   
1  51483ee8e4b06af4b55605bb  kingsminor bistrot       55.945272   
2  4c4c67949e6dbe9a15c9700d    Porto Restaurant       55.946333   
3  4bd0525e046076b02fb36f71        Costa Coffee       55.933625   
4  54982260498ec9dc36acb134            Chiquito       55.934879   

   Venue Longitude        Venue Category                   geometry  
0        -3.096077             Gastropub  POINT (-3.09608 55.94454)  
1        -3.096003        Breakfast Spot  POINT (-3.09600 55.94527)  
2        -3.084878  Fast Food Restaurant  POINT (-3.08488 55.94633)  
3        -3.105237           Coffee Shop  POINT (-3.10524 55.93363)  
4        -3.105460    Mexican Restaurant  POINT (-3.10546 55.93488)

Define a function to find which neighbourhood the venue is really in.

In [41]:
def which_neighbourhood(test_point):
    for i in range(154):
        if df["geometry"].contains(test_point)[i] == True:
            return df["NATURALCOM"][i]

Run the function for every row of the data frame and drop any rows where the neighbourhood label is not accurate in terms of the natural neighbourhood boundary.

In [42]:
print(edinburgh_venues_geo.shape)
for ind in edinburgh_venues_geo.index:
    location = edinburgh_venues_geo['geometry'][ind]
    if edinburgh_venues_geo['Neighbourhood'][ind] != which_neighbourhood(location):
        edinburgh_venues_geo.drop(ind, inplace = True)
edinburgh_venues_geo.reset_index(inplace = True)
edinburgh_venues_geo.drop(["index"], axis=1, inplace = True)
print(edinburgh_venues_geo.shape)
edinburgh_venues_geo.head()

(4859, 9)
(792, 9)


Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0  Brunstane/Gilberstoun               55.940545                -3.092460   
1  Brunstane/Gilberstoun               55.940545                -3.092460   
2  Brunstane/Gilberstoun               55.940545                -3.092460   
3           Newcraighall               55.934650                -3.088188   
4              Magdalene               55.942010                -3.108687   

                   Venue ID        Venue  Venue Latitude  Venue Longitude  \
0  54b97471498e26d1ad55ee73     Bar Zest       55.944542        -3.096077   
1  4cdd6bd114119eb02a35ed33  Burger King       55.942378        -3.101092   
2  4e0b733ab0fbc7fb0be0d383      Options       55.944675        -3.096049   
3  4c417b3aaf052d7fd7707d79  Cuddie Brae       55.934582        -3.094717   
4  5c5ad7729deb7d002cfec3db   Alexandros       55.942157        -3.109470   

         Venue Category                   geometry  
0             Gastropub  POINT (-3.09608 55.94454)  
1  Fast Food Restaurant  POINT (-3.10109 55.94238)  
2            Restaurant  POINT (-3.09605 55.94467)  
3            Restaurant  POINT (-3.09472 55.93458)  
4                  Café  POINT (-3.10947 55.94216)

Map all venues that are still being used.

In [43]:
m = folium.Map(location=[55.9533, -3.1883], zoom_start=10, tiles='CartoDB positron')

for _, r in df.iterrows():
    sim_geo = gpd.GeoSeries(r['geometry'])
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j,
                           style_function=lambda x: {'fillColor': 'orange'})
    folium.Popup(r['NATURALCOM']).add_to(geo_j)
    geo_j.add_to(m)

for _, r in edinburgh_venues_geo.iterrows():
    yo = folium.Marker(location=[r['Venue Latitude'], r['Venue Longitude']], popup='name: {}'.format(r['Venue']))
    yo.add_to(m)
m

Now to add a column with additional data about each venue.

In [44]:
#returns the price tier and likes count of the venues.

def furtherDetails(venue_id):
    url = 'https://api.foursquare.com/v2/venues/{}?&client_id={}&client_secret={}&v={}'.format(venue_id,CLIENT_ID, CLIENT_SECRET,VERSION)
    results = requests.get(url).json()
    try:
        return results['response']['venue']['attributes']['groups'][0]['items'][0]['priceTier'], results['response']['venue']['likes']['count']
    except:
        return "oops!", "oh no!" #if the data is strangely formatted for this venue.

In [45]:
edinburgh_venues_geo['price tier','likes'] = edinburgh_venues_geo['Venue ID'].apply(furtherDetails) #apply the above function
edinburgh_venues_geo.head()


Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0  Brunstane/Gilberstoun               55.940545                -3.092460   
1  Brunstane/Gilberstoun               55.940545                -3.092460   
2  Brunstane/Gilberstoun               55.940545                -3.092460   
3           Newcraighall               55.934650                -3.088188   
4              Magdalene               55.942010                -3.108687   

                   Venue ID        Venue  Venue Latitude  Venue Longitude  \
0  54b97471498e26d1ad55ee73     Bar Zest       55.944542        -3.096077   
1  4cdd6bd114119eb02a35ed33  Burger King       55.942378        -3.101092   
2  4e0b733ab0fbc7fb0be0d383      Options       55.944675        -3.096049   
3  4c417b3aaf052d7fd7707d79  Cuddie Brae       55.934582        -3.094717   
4  5c5ad7729deb7d002cfec3db   Alexandros       55.942157        -3.109470   

         Venue Category                   geometry (price tier, likes)  
0             Gastropub  POINT (-3.09608 55.94454)              (3, 0)  
1  Fast Food Restaurant  POINT (-3.10109 55.94238)              (1, 0)  
2            Restaurant  POINT (-3.09605 55.94467)              (2, 0)  
3            Restaurant  POINT (-3.09472 55.93458)              (2, 9)  
4                  Café  POINT (-3.10947 55.94216)              (1, 0)

In [46]:
edinburgh_venues_geo.columns
oopsy = edinburgh_venues_geo[edinburgh_venues_geo[('price tier', 'likes')] == ('oops!', 'oh no!')]
print(oopsy.shape)
print(edinburgh_venues_geo.shape)

(56, 10)
(792, 10)


The  number of rows without price tier and likes is relatively small. Need to check if they are evenly or unevenly distributed.

In [30]:
print(oopsy['Neighbourhood'].value_counts().head())
print(oopsy['Neighbourhood'].value_counts().tail())

Canonmills                   4
Portobello                   4
South Gyle/Edinburgh Park    4
Stockbridge                  3
Hillside/Easter Rd           3
Name: Neighbourhood, dtype: int64
Fairmilehead/Swanston    1
Braids                   1
Morningside              1
Gracemount               1
Corstorphine             1
Name: Neighbourhood, dtype: int64


The rows with missing data are pretty much evenly distributed  between  the neighbourhoods and so will be dropped from the dataframe.

In [49]:
indexNames = edinburgh_venues_geo[edinburgh_venues_geo[('price tier', 'likes')] == ('oops!', 'oh no!')].index
edinburgh_venues_geo.drop(indexNames , inplace=True)
edinburgh_venues_geo.head()

Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0  Brunstane/Gilberstoun               55.940545                -3.092460   
1  Brunstane/Gilberstoun               55.940545                -3.092460   
2  Brunstane/Gilberstoun               55.940545                -3.092460   
3           Newcraighall               55.934650                -3.088188   
4              Magdalene               55.942010                -3.108687   

                   Venue ID        Venue  Venue Latitude  Venue Longitude  \
0  54b97471498e26d1ad55ee73     Bar Zest       55.944542        -3.096077   
1  4cdd6bd114119eb02a35ed33  Burger King       55.942378        -3.101092   
2  4e0b733ab0fbc7fb0be0d383      Options       55.944675        -3.096049   
3  4c417b3aaf052d7fd7707d79  Cuddie Brae       55.934582        -3.094717   
4  5c5ad7729deb7d002cfec3db   Alexandros       55.942157        -3.109470   

         Venue Category                   geometry (price tier, likes)  
0             Gastropub  POINT (-3.09608 55.94454)              (3, 0)  
1  Fast Food Restaurant  POINT (-3.10109 55.94238)              (1, 0)  
2            Restaurant  POINT (-3.09605 55.94467)              (2, 0)  
3            Restaurant  POINT (-3.09472 55.93458)              (2, 9)  
4                  Café  POINT (-3.10947 55.94216)              (1, 0)

Check the above has done the expected operation:

In [50]:
edinburgh_venues_geo.columns
oopsy = edinburgh_venues_geo[edinburgh_venues_geo[('price tier', 'likes')] == ('oops!', 'oh no!')]
print(oopsy.shape)
print(edinburgh_venues_geo.shape)

(0, 10)
(736, 10)


The following splits the price tier and likes column into separate columns. 

In [72]:
edinburgh_venues_geo[('price tier','likes')]=edinburgh_venues_geo[('price tier','likes')].astype('string')

re.findall("[0-9]*",edinburgh_venues_geo[('price tier','likes')][0])
#print(re.findall("[0-9]+","(12, 0)"))

def price_extractor(text):
    numberList = re.findall("[0-9]+",text)
    return numberList[0]

def likes_extractor(text):
    numberList = re.findall("[0-9]+",text)
    return numberList[0]

edinburgh_venues_geo['price tier'] = edinburgh_venues_geo[('price tier','likes')].apply(lambda x: price_extractor(x))
edinburgh_venues_geo['likes'] = edinburgh_venues_geo[('price tier','likes')].apply(lambda x: likes_extractor(x))
edinburgh_venues_geo.head()

Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0  Brunstane/Gilberstoun               55.940545                -3.092460   
1  Brunstane/Gilberstoun               55.940545                -3.092460   
2  Brunstane/Gilberstoun               55.940545                -3.092460   
3           Newcraighall               55.934650                -3.088188   
4              Magdalene               55.942010                -3.108687   

                   Venue ID        Venue  Venue Latitude  Venue Longitude  \
0  54b97471498e26d1ad55ee73     Bar Zest       55.944542        -3.096077   
1  4cdd6bd114119eb02a35ed33  Burger King       55.942378        -3.101092   
2  4e0b733ab0fbc7fb0be0d383      Options       55.944675        -3.096049   
3  4c417b3aaf052d7fd7707d79  Cuddie Brae       55.934582        -3.094717   
4  5c5ad7729deb7d002cfec3db   Alexandros       55.942157        -3.109470   

         Venue Category                   geometry (price tier, likes)  \
0             Gastropub  POINT (-3.09608 55.94454)              (3, 0)   
1  Fast Food Restaurant  POINT (-3.10109 55.94238)              (1, 0)   
2            Restaurant  POINT (-3.09605 55.94467)              (2, 0)   
3            Restaurant  POINT (-3.09472 55.93458)              (2, 9)   
4                  Café  POINT (-3.10947 55.94216)              (1, 0)   

  price tier likes  
0          3     3  
1          1     1  
2          2     2  
3          2     2  
4          1     1

Use get_dummies to say which type of venue each venue is.

In [78]:
edinburgh_venues_geo.to_csv('/Users/emmaelley/Documents/GeoBackUpEdinFood.csv')

In [73]:
edinburgh_venues_geo = pd.read_csv('/Users/emmaelley/Documents/GeoBackUpEdinFood.csv')
edinburgh_venues_geo.shape

(736, 13)

In [74]:
list_to_discard = edinburgh_venues_geo.value_counts('Neighbourhood')[edinburgh_venues_geo.value_counts('Neighbourhood')<5].index.tolist()
print(list_to_discard)
edinburgh_venues_geo.set_index('Neighbourhood', inplace=True)
edinburgh_venues_geo.drop(list_to_discard, axis = 0, inplace=True)
edinburgh_venues_geo.reset_index(inplace=True)
print(edinburgh_venues_geo.shape)
edinburgh_venues_geo.head()

['The Inch', 'North Sighthill', 'Trinity', 'Viewforth', 'Leith Links', 'Merchiston and Myreside', 'Liberton', 'Prestonfield', 'Juniper Green', 'Comiston', 'Calders', 'Cramond', 'Bonnington', 'Stenhouse/Saughton', 'Brunstane/Gilberstoun', 'Wester Hailes', 'Calton Hill', 'Dumbiedykes', 'Restalrig', 'Redhall/Inglis Green', 'Polwarth', 'Pilton/Royston', 'Corstorphine/Craigmount', 'Parkhead', 'Craigentinny', 'Sciennes', 'Lauriston/Quartermile', 'Mortonhall', 'Fernieside/Ferniehill', 'Gilmerton', 'Longstone', 'Fountainbridge', 'Crewe Toll', 'Colinton/Bonaly', 'Kirkliston', 'Magdalene', 'Carrick Knowe', 'Fairmilehead/Swanston', 'Balgreen/Saughtonhall', 'Wester Coates', 'Broomhouse', 'Riccarton and Hermiston', 'Braids', 'Boswall/Wardie', 'Duddingston/The Durhams', 'Lochend', 'Southhouse', 'Bellevue/Broughton', 'Balerno', 'Kingsknowe', 'Blackford', 'Seafield', 'Burdiehouse', 'Baberton', 'Silverknowes', 'Sighthill', 'Marionville', 'Grange', 'Churchill and Greenhill', 'Ratho', 'Corstorphine/North

Neighbourhood  Unnamed: 0  Neighbourhood Latitude  Neighbourhood Longitude  \
0     Newbridge           6               55.939694                -3.421174   
1     Newbridge           7               55.939694                -3.421174   
2     Newbridge           8               55.939694                -3.421174   
3     Newbridge           9               55.939694                -3.421174   
4     Newbridge          10               55.939694                -3.421174   

                   Venue ID       Venue  Venue Latitude  Venue Longitude  \
0  4c9ddd7354c8a1cd47a8874b  McDonald's       55.937737        -3.402334   
1  5977930b1f744007e7bb5a5d      Subway       55.937586        -3.402917   
2  4d3ff9a41bd2a14305f8ed7c        3663       55.931507        -3.405493   
3  4e0883af18a8382643bad36b      Greggs       55.925187        -3.421631   
4  4f8528c3e4b062a5562c6f9f      Greggs       55.935652        -3.402666   

         Venue Category                                        geometry  \
0  Fast Food Restaurant                     POINT (-3.402334 55.937737)   
1        Sandwich Place   POINT (-3.402916516387222 55.937585695056214)   
2            Restaurant   POINT (-3.4054931077616715 55.93150734177571)   
3                Bakery  POINT (-3.4216314410160686 55.925186725655664)   
4                Bakery  POINT (-3.4026658241764265 55.935651541188335)   

  ('price tier', 'likes')  price tier  likes  
0                 (1, 21)           1      1  
1                  (1, 1)           1      1  
2                  (2, 0)           2      2  
3                  (1, 0)           1      1  
4                  (1, 2)           1      1

In [75]:
edin_onehot = pd.get_dummies(edinburgh_venues_geo['Venue Category'])
#, prefix="", prefix_sep=""
edin_onehot['likes'] = edinburgh_venues_geo['likes']
#Move the Neighbourhood column to the start.
fixed_columns = [edin_onehot.columns[-1]] + list(edin_onehot.columns[:-1])
edin_onehot = edin_onehot[fixed_columns]
edin_onehot['Neighbourhood'] = edinburgh_venues_geo['Neighbourhood']
fixed_columns = [edin_onehot.columns[-1]] + list(edin_onehot.columns[:-1])
edin_onehot = edin_onehot[fixed_columns]
edin_onehot.head(5)


Neighbourhood  likes  African Restaurant  American Restaurant  \
0     Newbridge      1                   0                    0   
1     Newbridge      1                   0                    0   
2     Newbridge      2                   0                    0   
3     Newbridge      1                   0                    0   
4     Newbridge      1                   0                    0   

   Asian Restaurant  Australian Restaurant  BBQ Joint  Bagel Shop  Bakery  \
0                 0                      0          0           0       0   
1                 0                      0          0           0       0   
2                 0                      0          0           0       0   
3                 0                      0          0           0       1   
4                 0                      0          0           0       1   

   Bar  ...  Snack Place  Spanish Restaurant  Steakhouse  Sushi Restaurant  \
0    0  ...            0                   0           0                 0   
1    0  ...            0                   0           0                 0   
2    0  ...            0                   0           0                 0   
3    0  ...            0                   0           0                 0   
4    0  ...            0                   0           0                 0   

   Taco Place  Tea Room  Thai Restaurant  Turkish Restaurant  \
0           0         0                0                   0   
1           0         0                0                   0   
2           0         0                0                   0   
3           0         0                0                   0   
4           0         0                0                   0   

   Vegetarian / Vegan Restaurant  Vietnamese Restaurant  
0                              0                      0  
1                              0                      0  
2                              0                      0  
3                              0                      0  
4                              0                      0  

[5 rows x 56 columns]

In [76]:
edin_onehot.to_csv('/Users/emmaelley/Documents/OneHotBackUpEdinFood.csv')

Sum over each type of venue and only keep venues with more than 5 occurences. 

In [77]:
summed = edin_onehot.sum().drop(["Neighbourhood","likes"])

print(summed.shape)

list_to_use = ["Neighbourhood"]

for i in range(len(summed)):
    if summed[i]>8:
        list_to_use.append(edin_onehot.columns[i+1])
list_to_use

(54,)


['Neighbourhood',
 'Bagel Shop',
 'Bakery',
 'Bistro',
 'Breakfast Spot',
 'Burrito Place',
 'Café',
 'Cocktail Bar',
 'Donut Shop',
 'Fast Food Restaurant',
 'French Restaurant',
 'Ice Cream Shop',
 'Indian Restaurant',
 'Middle Eastern Restaurant',
 'Pub',
 'Restaurant']

In [78]:
edin_onehot.head()

Neighbourhood  likes  African Restaurant  American Restaurant  \
0     Newbridge      1                   0                    0   
1     Newbridge      1                   0                    0   
2     Newbridge      2                   0                    0   
3     Newbridge      1                   0                    0   
4     Newbridge      1                   0                    0   

   Asian Restaurant  Australian Restaurant  BBQ Joint  Bagel Shop  Bakery  \
0                 0                      0          0           0       0   
1                 0                      0          0           0       0   
2                 0                      0          0           0       0   
3                 0                      0          0           0       1   
4                 0                      0          0           0       1   

   Bar  ...  Snack Place  Spanish Restaurant  Steakhouse  Sushi Restaurant  \
0    0  ...            0                   0           0                 0   
1    0  ...            0                   0           0                 0   
2    0  ...            0                   0           0                 0   
3    0  ...            0                   0           0                 0   
4    0  ...            0                   0           0                 0   

   Taco Place  Tea Room  Thai Restaurant  Turkish Restaurant  \
0           0         0                0                   0   
1           0         0                0                   0   
2           0         0                0                   0   
3           0         0                0                   0   
4           0         0                0                   0   

   Vegetarian / Vegan Restaurant  Vietnamese Restaurant  
0                              0                      0  
1                              0                      0  
2                              0                      0  
3                              0                      0  
4                              0                      0  

[5 rows x 56 columns]

In [79]:
edin_grouped = edin_onehot[list_to_use]
edin_grouped = edin_grouped.groupby('Neighbourhood').mean()
print(edin_grouped)

                                                Bagel Shop    Bakery  \
Neighbourhood                                                          
Abbeyhill                                         0.000000  0.000000   
Bankhead                                          0.000000  0.181818   
Barnton                                           0.000000  0.000000   
Blackhall                                         0.000000  0.000000   
Broughton Rd/Powderhall                           0.000000  0.000000   
Bruntsfield                                       0.000000  0.000000   
Cameron Toll                                      0.000000  0.125000   
Canongate                                         0.000000  0.083333   
Canonmills                                        0.000000  0.083333   
Chesser                                           0.000000  0.090909   
Clermiston/Drumbrae                               0.000000  0.166667   
Comely Bank                                       0.000000  0.28

In [80]:
edin_grouped = edin_onehot[list_to_use]
edin_grouped = edin_grouped.groupby('Neighbourhood', as_index=False).mean()
print(edin_grouped)

                                     Neighbourhood  Bagel Shop    Bakery  \
0                                        Abbeyhill    0.000000  0.000000   
1                                         Bankhead    0.000000  0.181818   
2                                          Barnton    0.000000  0.000000   
3                                        Blackhall    0.000000  0.000000   
4                          Broughton Rd/Powderhall    0.000000  0.000000   
5                                      Bruntsfield    0.000000  0.000000   
6                                     Cameron Toll    0.000000  0.125000   
7                                        Canongate    0.000000  0.083333   
8                                       Canonmills    0.000000  0.083333   
9                                          Chesser    0.000000  0.090909   
10                             Clermiston/Drumbrae    0.000000  0.166667   
11                                     Comely Bank    0.000000  0.285714   
12          

In [81]:

num_top_venues = 3

def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    print(row_categories)
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighbourhoods_venues_sorted = pd.DataFrame(columns=columns)
neighbourhoods_venues_sorted['Neighbourhood'] = edin_grouped['Neighbourhood']

for ind in np.arange(edin_grouped.shape[0]):
    neighbourhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(edin_grouped.iloc[ind, :], num_top_venues)
    
neighbourhoods_venues_sorted.head()


Bagel Shop                   0.0
Bakery                       0.0
Bistro                       0.0
Breakfast Spot               0.0
Burrito Place                0.0
Café                         0.3
Cocktail Bar                 0.0
Donut Shop                   0.0
Fast Food Restaurant         0.1
French Restaurant            0.0
Ice Cream Shop               0.0
Indian Restaurant            0.0
Middle Eastern Restaurant    0.0
Pub                          0.0
Restaurant                   0.0
Name: 0, dtype: object
Bagel Shop                        0.0
Bakery                       0.181818
Bistro                            0.0
Breakfast Spot                    0.0
Burrito Place                     0.0
Café                         0.090909
Cocktail Bar                      0.0
Donut Shop                   0.090909
Fast Food Restaurant         0.181818
French Restaurant                 0.0
Ice Cream Shop                    0.0
Indian Restaurant                 0.0
Middle Eastern Restaurant 

Neighbourhood 1st Most Common Venue 2nd Most Common Venue
0                Abbeyhill                  Café  Fast Food Restaurant
1                 Bankhead                Bakery  Fast Food Restaurant
2                  Barnton                  Café     Indian Restaurant
3                Blackhall     Indian Restaurant                  Café
4  Broughton Rd/Powderhall                  Café            Bagel Shop

In [82]:
# set number of clusters
kclusters = 15

edin_grouped_clustering = edin_grouped
edin_grouped_clustering = edin_grouped.drop(['Neighbourhood'], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=1).fit(edin_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

/var/folders/5x/2qszld594pgblwbdbl9wmmxh0000gn/T/ipykernel_96598/3147171792.py:5: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  edin_grouped_clustering = edin_grouped.drop(['Neighbourhood'], 1)


array([2, 1, 6, 4, 5, 5, 1, 5, 3, 5], dtype=int32)

In [83]:
# add clustering labels
neighbourhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
edin_merged = df[['NATURALCOM','lat','lon','geometry']]

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
edin_merged = edin_merged.join(neighbourhoods_venues_sorted.set_index('Neighbourhood'), on='NATURALCOM')

print(edin_merged)
edin_merged.head(20) # check the last columns!


#print(edin_merged.shape)
edin_merged.dropna(axis=0, how='any', thresh=None, subset=None, inplace=True)

                    NATURALCOM        lat       lon  \
0        Brunstane/Gilberstoun  55.940545 -3.092460   
1                 Newcraighall  55.934650 -3.088188   
2                    Magdalene  55.942010 -3.108687   
3                    Newbridge  55.939694 -3.421174   
4           Cammo/Strathalmond  55.958395 -3.324203   
..                         ...        ...       ...   
149    Corstorphine/Craigmount  55.948396 -3.299799   
150               Corstorphine  55.942325 -3.282735   
151      Corstorphine/Clerwood  55.950484 -3.280013   
152  The Christians/Portobello  55.945476 -3.106248   
153      Ferryfield/Inverleith  55.970581 -3.224060   

                                              geometry  Cluster Labels  \
0    POLYGON ((-3.10276 55.94435, -3.10276 55.94435...             NaN   
1    MULTIPOLYGON (((-3.09979 55.93598, -3.09855 55...             NaN   
2    POLYGON ((-3.10240 55.94088, -3.10245 55.94165...             NaN   
3    POLYGON ((-3.41296 55.95159, -3.41414 

In [87]:
# create map
map_clusters = folium.Map(location=[55.9533, -3.1883], zoom_start=10, tiles='CartoDB positron')

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.tab20(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# set colour scheme for neighbourhoods
#colors_array2 = cm.coolwarm(np.linspace(0, 1,120))
#colourscheme = [colors.rgb2hex(i) for i in colors_array2]

# add markers to the map
for lat, lon, poi, cluster, top1, top2, top3, sim_geo in zip(edin_merged['lat'], edin_merged['lon'], edin_merged['NATURALCOM'], edin_merged['Cluster Labels'], edin_merged['1st Most Common Venue'], edin_merged['2nd Most Common Venue'], edin_merged['3rd Most Common Venue'],edin_merged['geometry']):
    
    geo_j = gpd.GeoSeries(sim_geo).to_json()
    style = {'fillColor': '#fcbbf6','fillOpacity': 0.2, 'color': '#fcbbf6', 'opacity':0.4}
    geo_j = folium.GeoJson(data=geo_j, style_function = lambda x: style)
    folium.Popup(poi).add_to(geo_j)
    geo_j.add_to(map_clusters)
    label = folium.Popup(str(poi) +'-------' + ' Cluster ' + str(cluster) + '-------' + '\n Top venue categories: ' + '\n'+ str(top1) , parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster-1)],
        fill=True,
        fill_color=rainbow[int(cluster-1)],
        fill_opacity=0.7).add_to(map_clusters)
#folium.LayerControl().add_to(map_clusters)
        
map_clusters

#geopandas.GeoSeries([shapely_polygon]).to_json()

In [80]:
edin_merged[edin_merged["NATURALCOM"].str.contains("Leith")]

NATURALCOM        lat       lon  \
68   Leith/Easter Rd  55.964204 -3.170005   
112            Leith  55.978887 -3.168427   
113      Leith Links  55.967706 -3.157673   

                                              geometry  Cluster Labels  \
68   POLYGON ((-3.17296 55.96908, -3.17297 55.96908...             2.0   
112  POLYGON ((-3.18168 55.99236, -3.18609 55.99082...             4.0   
113  POLYGON ((-3.16618 55.96763, -3.16591 55.96743...             2.0   

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
68                 Bakery     Indian Restaurant    Italian Restaurant   
112                  Café    Seafood Restaurant                Bakery   
113    Chinese Restaurant  Fast Food Restaurant     Indian Restaurant   

     Number density  
68         0.164817  
112        0.020642  
113        0.080666